In [1]:
from pymongo import MongoClient
import pandas as pd

In [2]:
def connectCollection(database, collection):
    client = MongoClient()
    db = client[database]
    coll = db[collection]
    return db, coll


In [3]:
db, coll = connectCollection('companies','companies')

In [31]:
#rest = list(coll.find({'founded_year':{'$gt':2009}}))
new_companies = list(coll.find({'$and':
                           [ { "offices.latitude": {"$exists": True,"$ne":None} },
                            { "offices.longitude": {"$exists": True,"$ne":None} },
                            {'founded_year': {'$gt': 2009 }},
                            {'deadpooled_year':None},
                            {'$or':[{'category_code': 'advertising' },
                                    {'category_code': 'mobile' },
                                    {'category_code': 'web' },
                                    {'category_code': 'games_video' }]}]}, 
                          {'name':1,'founded_year': 1, '_id': 0,'offices.latitude':1, 
                           'offices.longitude':1, 'category_code':1, 'location':1 }))

In [34]:
print(len(new_companies))

29


In [33]:
new_companies[0]

{'category_code': 'web',
 'founded_year': 2011,
 'name': 'Mokitown',
 'offices': [{'latitude': 37.09024, 'longitude': -95.712891}]}

In [36]:
df = pd.DataFrame(new_companies)
df

category_code  founded_year                   name  \
0            web          2011               Mokitown   
1         mobile          2010                  GENWI   
2            web          2013                  Fixya   
3    games_video          2011  Social Gaming Network   
4         mobile          2012                Skydeck   
5         mobile          2012  Jumbuck Entertainment   
6            web          2010                 Pixsta   
7    games_video          2011                   Fuzz   
8            web          2010           CollegeConvo   
9            web          2011                 Ziippi   
10   games_video          2010           Titan Gaming   
11   advertising          2013               SEOGroup   
12        mobile          2010                 vufind   
13   games_video          2011                  Kidos   
14        mobile          2010                 vufind   
15   games_video          2011                  Kidos   
16   games_video          2010                Equedia   
17   advertising          2010             Webmoblink   
18           web          2010                  Yipit   
19           web          2010                  fruux   
20           web          2013                 Clowdy   
21   games_video          2010               Tengaged   
22   games_video          2010                  Indee   
23           web          2010            eCampusCash   
24   games_video          2010            BASH Gaming   
25   advertising          2010                MyLikes   
26   games_video          2011          Hayen Company   
27   games_video          2010                 Flixxy   
28   games_video          2010            ekidnaworld   

                                              offices  
0   [{'longitude': -95.712891, 'latitude': 37.09024}]  
1     [{'longitude': -111.9035, 'latitude': 33.8171}]  
2   [{'longitude': -122.323895, 'latitude': 37.566...  
3   [{'longitude': -122.161523, 'latitude': 37.446...  
4   [{'longitude': -122.3254705, 'latitude': 37.56...  
5   [{'longitude': 144.962991, 'latitude': -37.817...  
6    [{'longitude': -0.208979, 'latitude': 51.51819}]  
7   [{'longitude': -122.387799, 'latitude': 37.760...  
8   [{'longitude': -74.294395, 'latitude': 40.6502...  
9   [{'longitude': -122.1612868, 'latitude': 37.44...  
10  [{'longitude': -113.515769, 'latitude': 53.544...  
11  [{'longitude': -87.624701, 'latitude': 41.8862...  
12  [{'longitude': -122.145153, 'latitude': 37.424...  
13  [{'longitude': -73.956599, 'latitude': 40.7680...  
14  [{'longitude': -122.145153, 'latitude': 37.424...  
15  [{'longitude': -73.956599, 'latitude': 40.7680...  
16  [{'longitude': -123.1169693, 'latitude': 49.28...  
17  [{'longitude': -80.424167, 'latitude': 25.6558...  
18  [{'longitude': -73.987764, 'latitude': 40.7446...  
19  [{'longitude': 7.6267552, 'latitude': 51.96300...  
20  [{'longitude': -2.2439492, 'latitude': 53.4837...  
21  [{'longitude': 2.1634249, 'latitude': 41.42412...  
22  [{'longitude': -122.4052761, 'latitude': 37.80...  
23  [{'longitude': -74.294395, 'latitude': 40.6502...  
24  [{'longitude': -122.0780632, 'latitude': 37.55...  
25  [{'longitude': -122.408914, 'latitude': 37.777...  
26  [{'longitude': -81.004871, 'latitude': 34.0191...  
27  [{'longitude': -82.800333, 'latitude': 27.9723...  
28  [{'longitude': 153.033686, 'latitude': -27.457...

In [37]:
#funcion para sacar las coordinadas
def getLocation(company):
    longitude = company['offices'][0]['longitude']
    latitude = company['offices'][0]['latitude']
    coordinates = [float(longitude), float(latitude)]
    
    return coordinates

In [38]:
getLocation(new_companies[0])

[-95.712891, 37.09024]

In [39]:
coords=[{'type': 'Point', 'coordinates':getLocation(comp)}for comp in new_companies]

In [17]:
#print(coords)

In [40]:
df['office_coords']=coords
df.head()

category_code  founded_year                   name  \
0           web          2011               Mokitown   
1        mobile          2010                  GENWI   
2           web          2013                  Fixya   
3   games_video          2011  Social Gaming Network   
4        mobile          2012                Skydeck   

                                             offices  \
0  [{'longitude': -95.712891, 'latitude': 37.09024}]   
1    [{'longitude': -111.9035, 'latitude': 33.8171}]   
2  [{'longitude': -122.323895, 'latitude': 37.566...   
3  [{'longitude': -122.161523, 'latitude': 37.446...   
4  [{'longitude': -122.3254705, 'latitude': 37.56...   

                                       office_coords  
0  {'coordinates': [-95.712891, 37.09024], 'type'...  
1  {'coordinates': [-111.9035, 33.8171], 'type': ...  
2  {'coordinates': [-122.323895, 37.566879], 'typ...  
3  {'coordinates': [-122.161523, 37.446823], 'typ...  
4  {'coordinates': [-122.3254705, 37.5645375], 't...

In [41]:
df=df[['category_code','founded_year','name','office_coords']]

In [42]:
df.head()

category_code  founded_year                   name  \
0           web          2011               Mokitown   
1        mobile          2010                  GENWI   
2           web          2013                  Fixya   
3   games_video          2011  Social Gaming Network   
4        mobile          2012                Skydeck   

                                       office_coords  
0  {'coordinates': [-95.712891, 37.09024], 'type'...  
1  {'coordinates': [-111.9035, 33.8171], 'type': ...  
2  {'coordinates': [-122.323895, 37.566879], 'typ...  
3  {'coordinates': [-122.161523, 37.446823], 'typ...  
4  {'coordinates': [-122.3254705, 37.5645375], 't...

In [43]:
df.to_json('df_new_compannies.json', orient='records')

In [45]:
old_companies = list(coll.find({'$and':
                           [ { "offices.latitude": {"$exists": True,"$ne":None} },
                            { "offices.longitude": {"$exists": True,"$ne":None} },
                            {'founded_year': {'$lt': 2009 }},
                            {'deadpooled_year':None}]}, 
                          {'name':1,'founded_year': 1, '_id': 0,'offices.latitude':1, 
                           'offices.longitude':1, 'category_code':1, 'location':1 }))

In [47]:
len(old_companies)

6578

In [50]:
df_oldcomp = pd.DataFrame(old_companies)
df_oldcomp.head()

category_code  founded_year             name  \
0           web          2001  TechnologyGuide   
1          news          2004             Digg   
2        social          2004         Facebook   
3           web          1999          Postini   
4           web          2006             Geni   

                                             offices  
0  [{'longitude': -84.351532, 'latitude': 39.06685}]  
1  [{'longitude': -122.394523, 'latitude': 37.764...  
2  [{'longitude': -122.151801, 'latitude': 37.416...  
3  [{'longitude': -122.247573, 'latitude': 37.506...  
4  [{'longitude': -118.393064, 'latitude': 34.090...

In [52]:
old_coords=[{'type': 'Point', 'coordinates':getLocation(comp)}for comp in old_companies]

In [53]:
df_oldcomp['office_coords']=old_coords

In [55]:
df_oldcomp.head()

category_code  founded_year             name  \
0           web          2001  TechnologyGuide   
1          news          2004             Digg   
2        social          2004         Facebook   
3           web          1999          Postini   
4           web          2006             Geni   

                                             offices  \
0  [{'longitude': -84.351532, 'latitude': 39.06685}]   
1  [{'longitude': -122.394523, 'latitude': 37.764...   
2  [{'longitude': -122.151801, 'latitude': 37.416...   
3  [{'longitude': -122.247573, 'latitude': 37.506...   
4  [{'longitude': -118.393064, 'latitude': 34.090...   

                                       office_coords  
0  {'coordinates': [-84.351532, 39.06685], 'type'...  
1  {'coordinates': [-122.394523, 37.764726], 'typ...  
2  {'coordinates': [-122.151801, 37.41605], 'type...  
3  {'coordinates': [-122.247573, 37.506885], 'typ...  
4  {'coordinates': [-118.393064, 34.090368], 'typ...

In [56]:
df_oldcomp=df_oldcomp[['category_code','founded_year','name','office_coords']]

In [57]:
df_oldcomp.to_json('df_old_companies.json', orient='records')

In [ ]:
#esto una vez hemos añadido las coordenadas, para ver la distancia.

In [58]:
db, coll = connectCollection('companies','old_companies')

In [60]:
old_comp_paloalto = coll.find(
    {"office_coords":
     {"$near":
      {"$geometry":
       {"type":"Point",
        "coordinates":[-122.1722525,37.4374154]
       },
       "$minDistance":2000
      }
     }
    }
)
old_comp_paloalto=list(old_comp_paloalto)

In [61]:
print(len(old_comp_paloalto))

6521


In [63]:
import folium

In [64]:
map_city=folium.Map(location=[37.4374154,-122.1722525], zoom_start=12)
for c in old_comp_paloalto:
    folium.Marker(c['office_coords']['coordinates'][::-1],
                    radius=2,
                    icon=folium.Icon(icon='cloud',color='red'), 
                   ).add_to(map_city)



In [65]:
map_city

